# This is for the Final Project

In [33]:
#import required libraries
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

# for webscraping import Beautiful Soup 
from bs4 import BeautifulSoup

import xml

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
print('All libraries are imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

All libraries are imported.


# First Data Scraping

In [34]:
url_toronto = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
result = requests.get(url_toronto)
result.headers

{'Date': 'Wed, 04 Dec 2019 11:12:40 GMT', 'Server': 'mw1266.eqiad.wmnet', 'X-Powered-By': 'PHP/7.2.24-1+0~20191026.31+debian9~1.gbpbbacde+wmf1', 'X-Content-Type-Options': 'nosniff', 'P3P': 'CP="See https://en.wikipedia.org/wiki/Special:CentralAutoLogin/P3P for more info."', 'Content-language': 'en', 'Vary': 'Accept-Encoding,Cookie,Authorization', 'Last-Modified': 'Wed, 20 Nov 2019 11:12:40 GMT', 'Backend-Timing': 'D=103869 t=1575457960261013', 'Content-Type': 'text/html; charset=UTF-8', 'Content-Encoding': 'gzip', 'X-Varnish': '487907599, 286740457, 310580655 175388946', 'Age': '33934', 'X-Cache': 'cp1085 pass, cp3064 miss, cp3056 hit/4', 'X-Cache-Status': 'hit-front', 'Server-Timing': 'cache;desc="hit-front"', 'Strict-Transport-Security': 'max-age=106384710; includeSubDomains; preload', 'Set-Cookie': 'WMF-Last-Access=04-Dec-2019;Path=/;HttpOnly;secure;Expires=Sun, 05 Jan 2020 12:00:00 GMT, WMF-Last-Access-Global=04-Dec-2019;Path=/;Domain=.wikipedia.org;HttpOnly;secure;Expires=Sun, 05 

In [35]:
soup = BeautifulSoup(result.content, 'html.parser')

#### Tranform the data into a *pandas* dataframe and table design

In [36]:
table= soup.find('table')
all_fields = table.find_all('td')

postcode = []
borough = []
neighbourhood = []

for i in range(0, len(all_fields), 3):
    postcode.append(all_fields[i].text.strip())
    borough.append(all_fields[i+1].text.strip())
    neighbourhood.append(all_fields[i+2].text.strip())
        
dataframe= pd.DataFrame(data=[postcode, borough, neighbourhood]).transpose()
dataframe.columns = ['Postcode', 'Borough', 'Neighbourhood']
print(dataframe.shape)
dataframe.head()

(287, 3)


Postcode           Borough     Neighbourhood
0      M1A      Not assigned      Not assigned
1      M2A      Not assigned      Not assigned
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront

#### Remove "Not Assigned Values"

In [37]:
dataframe['Borough'].replace('Not assigned', np.nan, inplace=True)
dataframe.dropna(subset=['Borough'], inplace=True)
print(dataframe.shape)
dataframe.head()

(210, 3)


Postcode           Borough     Neighbourhood
2      M3A        North York         Parkwoods
3      M4A        North York  Victoria Village
4      M5A  Downtown Toronto      Harbourfront
5      M6A        North York  Lawrence Heights
6      M6A        North York    Lawrence Manor

In [38]:
#Group by Postcode, Borough
dataframe2= dataframe.groupby(['Postcode', 'Borough'])['Neighbourhood'].apply(', '.join).reset_index()
dataframe2.columns = ['Postcode', 'Borough', 'Neighbourhood']
print(dataframe2.shape)
dataframe2.head()

(103, 3)


Postcode      Borough                           Neighbourhood
0      M1B  Scarborough                          Rouge, Malvern
1      M1C  Scarborough  Highland Creek, Rouge Hill, Port Union
2      M1E  Scarborough       Guildwood, Morningside, West Hill
3      M1G  Scarborough                                  Woburn
4      M1H  Scarborough                               Cedarbrae

In [39]:
#add Latitude, Longitude 
geo_data = pd.read_csv('http://cocl.us/Geospatial_data')
geo_data.columns = ['Postcode', 'Latitude', 'Longitude']

In [40]:
last_table= pd.merge(dataframe2, geo_data, on=['Postcode'], how='inner')
toronto_table= last_table[['Borough', 'Neighbourhood', 'Postcode', 'Latitude', 'Longitude']].copy()
toronto_table.head()

Borough                           Neighbourhood Postcode   Latitude  \
0  Scarborough                          Rouge, Malvern      M1B  43.806686   
1  Scarborough  Highland Creek, Rouge Hill, Port Union      M1C  43.784535   
2  Scarborough       Guildwood, Morningside, West Hill      M1E  43.763573   
3  Scarborough                                  Woburn      M1G  43.770992   
4  Scarborough                               Cedarbrae      M1H  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

#### Use geopy library to get the latitude and longitude values of Toronto

In [41]:
address = 'Toronto'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


#### Create a map of Toronto with neighborhoods superimposed on top.

In [42]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(toronto_table['Latitude'], toronto_table['Longitude'], toronto_table['Borough'], toronto_table['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

#### Explore the neighbourhood

In [112]:
CLIENT_ID = 'id' # your Foursquare ID
CLIENT_SECRET = 'secret' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: id
CLIENT_SECRET:secret


In [44]:
new_t = toronto_table[toronto_table['Borough'].str.contains('Toronto')]
new_table = new_t.reset_index(drop=True)
new_table.head()

Borough                   Neighbourhood Postcode   Latitude  \
0     East Toronto                     The Beaches      M4E  43.676357   
1     East Toronto    The Danforth West, Riverdale      M4K  43.679557   
2     East Toronto  The Beaches West, India Bazaar      M4L  43.668999   
3     East Toronto                 Studio District      M4M  43.659526   
4  Central Toronto                   Lawrence Park      M4N  43.728020   

   Longitude  
0 -79.293031  
1 -79.352188  
2 -79.315572  
3 -79.340923  
4 -79.388790

In [45]:
#Look for the first neighbourhood
new_table.loc[0, 'Neighbourhood']

'The Beaches'

In [46]:
nfirst_latitude = new_table.loc[0, 'Latitude'] # neighbourhood latitude value
nfirst_longitude = new_table.loc[0, 'Longitude'] # neighbourhood longitude value

nfirst_name = new_table.loc[0, 'Neighbourhood'] # neighbourhood name

print('Latitude and longitude values of {} are {}, {}.'.format(nfirst_name, nfirst_longitude,nfirst_longitude))

Latitude and longitude values of The Beaches are -79.2930312, -79.2930312.


#### Now, let's get the top 100 venues that are in Lawrence Park within a radius of 500 meters.

In [47]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    nfirst_latitude, 
    nfirst_longitude, 
    radius, 
    LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?&client_id=ZZAUJXR2CVJAKYY1VXQE2RE1CCEJJZEXS5HKBKS12KV5VG3J&client_secret=SW4A1GDXF3MDV5SDAQ3KFJXOVXXSML10TR1BG4X5EC0RONQH&v=20180604&ll=43.67635739999999,-79.2930312&radius=500&limit=100'

In [48]:
#Send the get request
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5de8194e760a7f001b93569a'},
 'response': {'headerLocation': 'The Beaches',
  'headerFullLocation': 'The Beaches, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 4,
  'suggestedBounds': {'ne': {'lat': 43.680857404499996,
    'lng': -79.28682091449052},
   'sw': {'lat': 43.67185739549999, 'lng': -79.29924148550948}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4bd461bc77b29c74a07d9282',
       'name': 'Glen Manor Ravine',
       'location': {'address': 'Glen Manor',
        'crossStreet': 'Queen St.',
        'lat': 43.67682094413784,
        'lng': -79.29394208780985,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.67682094413784,
          'lng': -79.29394208780985}],
        'distanc

In [21]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [49]:
#Now it is time to clean the json and structure it into a *pandas* dataframe.
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name         categories        lat        lng
0                   Glen Manor Ravine              Trail  43.676821 -79.293942
1  The Big Carrot Natural Food Market  Health Food Store  43.678879 -79.297734
2                 Grover Pub and Grub                Pub  43.679181 -79.297215
3                       Upper Beaches       Neighborhood  43.680563 -79.292869

In [50]:
#how many venues returned by Foursquare
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

4 venues were returned by Foursquare.


In [51]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [111]:
#Search Mediterranean Restaurant
search_query = 'mediterranean'
print(search_query + ' .... OK!')

mediterranean .... OK!


In [60]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=ZZAUJXR2CVJAKYY1VXQE2RE1CCEJJZEXS5HKBKS12KV5VG3J&client_secret=SW4A1GDXF3MDV5SDAQ3KFJXOVXXSML10TR1BG4X5EC0RONQH&ll=43.653963,-79.387207&v=20180604&query=mediterranean&radius=1000&limit=100'

In [61]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5de81b2f1835dd001ba2cb70'},
 'response': {'venues': [{'id': '4cbc732b035d236ac1a2e54e',
    'name': 'Saha Mediterranean Fast Food',
    'location': {'address': '81 Gerrard St W',
     'crossStreet': 'La Plante Ave',
     'lat': 43.658497,
     'lng': -79.386035,
     'labeledLatLngs': [{'label': 'display',
       'lat': 43.658497,
       'lng': -79.386035}],
     'distance': 513,
     'postalCode': 'M7A 2H4',
     'cc': 'CA',
     'city': 'Toronto',
     'state': 'ON',
     'country': 'Canada',
     'formattedAddress': ['81 Gerrard St W (La Plante Ave)',
      'Toronto ON M7A 2H4',
      'Canada']},
    'categories': [{'id': '4bf58dd8d48988d1c0941735',
      'name': 'Mediterranean Restaurant',
      'pluralName': 'Mediterranean Restaurants',
      'shortName': 'Mediterranean',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/mediterranean_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1575492440',
   

In [62]:

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [66]:
#Get venues for all neighborhoods
toronto_venues = getNearbyVenues(names=new_table['Neighbourhood'],
                                latitudes=new_table['Latitude'],
                                longitudes=new_table['Longitude'])
toronto_venues.shape

The Beaches
The Danforth West, Riverdale
The Beaches West, India Bazaar
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park, Summerhill East
Deer Park, Forest Hill SE, Rathnelly, South Hill, Summerhill West
Rosedale
Cabbagetown, St. James Town
Church and Wellesley
Harbourfront
Ryerson, Garden District
St. James Town
Berczy Park
Central Bay Street
Adelaide, King, Richmond
Harbourfront East, Toronto Islands, Union Station
Design Exchange, Toronto Dominion Centre
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North, Forest Hill West
The Annex, North Midtown, Yorkville
Harbord, University of Toronto
Chinatown, Grange Park, Kensington Market
CN Tower, Bathurst Quay, Island airport, Harbourfront West, King and Spadina, Railway Lands, South Niagara
Stn A PO Boxes 25 The Esplanade
First Canadian Place, Underground city
Christie
Dovercourt Village, Dufferin
Little Portugal, Trinity
Brockton, Exhibition Place, Parkdale Village
High Park, The Junction Sout

(1686, 7)

In [68]:
#Check size and data
toronto_venues.shape
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                   The Beaches              43.676357   
1                   The Beaches              43.676357   
2                   The Beaches              43.676357   
3                   The Beaches              43.676357   
4  The Danforth West, Riverdale              43.679557   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -79.293031                   Glen Manor Ravine       43.676821   
1              -79.293031  The Big Carrot Natural Food Market       43.678879   
2              -79.293031                 Grover Pub and Grub       43.679181   
3              -79.293031                       Upper Beaches       43.680563   
4              -79.352188                            Pantheon       43.677621   

   Venue Longitude     Venue Category  
0       -79.293942              Trail  
1       -79.297734  Health Food Store  
2       -79.297215                Pub  
3       -79.292869       Neighborhood  
4       -79.351434   Greek Restaurant

In [69]:
#Number of venues based on the neighborhood
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Adelaide, King, Richmond                                              100   
Berczy Park                                                            57   
Brockton, Exhibition Place, Parkdale Village                           21   
Business Reply Mail Processing Centre 969 Eastern                      16   
CN Tower, Bathurst Quay, Island airport, Harbou...                     16   
Cabbagetown, St. James Town                                            46   
Central Bay Street                                                     85   
Chinatown, Grange Park, Kensington Market                              94   
Christie                                                               17   
Church and Wellesley                                                   83   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             37   
Davisville North                                                        9   
Deer Park, Forest Hill SE, Rathnelly, South Hil...                     15   
Design Exchange, Toronto Dominion Centre                              100   
Dovercourt Village, Dufferin                                           14   
First Canadian Place, Underground city                                100   
Forest Hill North, Forest Hill West                                     4   
Harbord, University of Toronto                                         35   
Harbourfront                                                           49   
Harbourfront East, Toronto Islands, Union Station                     100   
High Park, The Junction South                                          25   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               62   
Moore Park, Summerhill East                                             2   
North Toronto West                                                     19   
Parkdale, Roncesvalles                                                 14   
Rosedale                                                                4   
Roselawn                                                                1   
Runnymede, Swansea                                                     36   
Ryerson, Garden District                                              100   
St. James Town                                                        100   
Stn A PO Boxes 25 The Esplanade                                        98   
Studio District                                                        37   
The Annex, North Midtown, Yorkville                                    20   
The Beaches                                                             4   
The Beaches West, India Bazaar                                         20   
The Danforth West, Riverdale                                           43   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Adelaide, King, Richmond                                               100   
Berczy Park                                                             57   
Brockton, Exhibition Place, Parkdale Village                            21   
Business Reply Mail Processing Centre 969 Eastern                       16   
CN Tower, Bathurst Quay, Island airport, Harbou...                      16   
Cabbagetown, St. James Town                                             46   
Central Bay Street                                                      85   
Chinatown, Grange Park, Kensington Market                               94   
Christie                                                                17   
Church and Wellesley                                                    83   
Commerce Court, Victoria Hotel     

In [70]:
#what are the unique categories
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 234 uniques categories.


In [72]:
# Check if Middle Eastern Restaurant is one of the unique one
"Middle Eastern Restaurant" in toronto_venues['Venue Category'].unique()

True

In [73]:
second = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
second['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [second.columns[-1]] + list(second.columns[:-1])
second = second[fixed_columns]

print(second.shape)
second.head()

(1686, 235)


Neighborhoods  Afghan Restaurant  Airport  \
0                   The Beaches                  0        0   
1                   The Beaches                  0        0   
2                   The Beaches                  0        0   
3                   The Beaches                  0        0   
4  The Danforth West, Riverdale                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  \
0                 0                    0             0         0   
1                 0                    0             0         0   
2                 0                    0             0         0   
3                 0                    0             0         0   
4                 0                    0             0         0   

   Argentinian Restaurant  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0                       0            0                    0                 0   
1                       0            0                    0                 0   
2                       0            0                    0                 0   
3                       0            0                    0                 0   
4                       0            0                    0                 0   

   Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  \
0                   0              0          0           0           0   
1                   0              0          0           0           0   
2                   0              0          0           0           0   
3                   0              0          0           0           0   
4                   0              0          0           0           0   

   Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0       0     0    0                 0                   0      0   
1       0     0    0                 0                   0      0   
2       0     0    0                 0                   0      0   
3       0     0    0                 0                   0      0   
4       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bistro  \
0                0         0           0                   0       0   
1                0         0           0                   0       0   
2                0         0           0                   0       0   
3                0         0           0                   0       0   
4                0         0           0                   0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0           0              0          0         0                     0   
1           0              0          0         0                     0   
2           0              0          0         0                     0   
3           0              0          0         0                     0   
4           0              0          0         0                     0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Building  Burger Joint  \
0               0        0                0         0             0   
1               0        0                0         0             0   
2               0        0                0         0             0   
3               0        0                0         0             0   
4               0        0                0         0             0   

   Burrito Place  Bus Line  Butcher  Café  Cajun / Creole Restaurant  \
0              0         0        0     0                    

In [75]:
#Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
allgrouped = second.groupby(["Neighborhoods"]).mean().reset_index()
print(allgrouped.shape)
allgrouped

(38, 235)


Neighborhoods  Afghan Restaurant  \
0                            Adelaide, King, Richmond           0.000000   
1                                         Berczy Park           0.000000   
2        Brockton, Exhibition Place, Parkdale Village           0.000000   
3   Business Reply Mail Processing Centre 969 Eastern           0.000000   
4   CN Tower, Bathurst Quay, Island airport, Harbo...           0.000000   
5                         Cabbagetown, St. James Town           0.000000   
6                                  Central Bay Street           0.000000   
7           Chinatown, Grange Park, Kensington Market           0.000000   
8                                            Christie           0.000000   
9                                Church and Wellesley           0.012048   
10                     Commerce Court, Victoria Hotel           0.000000   
11                                         Davisville           0.000000   
12                                   Davisville North           0.000000   
13  Deer Park, Forest Hill SE, Rathnelly, South Hi...           0.000000   
14           Design Exchange, Toronto Dominion Centre           0.000000   
15                       Dovercourt Village, Dufferin           0.000000   
16             First Canadian Place, Underground city           0.000000   
17                Forest Hill North, Forest Hill West           0.000000   
18                     Harbord, University of Toronto           0.000000   
19                                       Harbourfront           0.000000   
20  Harbourfront East, Toronto Islands, Union Station           0.000000   
21                      High Park, The Junction South           0.000000   
22                                      Lawrence Park           0.000000   
23                           Little Portugal, Trinity           0.000000   
24                        Moore Park, Summerhill East           0.000000   
25                                 North Toronto West           0.000000   
26                             Parkdale, Roncesvalles           0.000000   
27                                           Rosedale           0.000000   
28                                           Roselawn           0.000000   
29                                 Runnymede, Swansea           0.000000   
30                           Ryerson, Garden District           0.000000   
31                                     St. James Town           0.000000   
32                    Stn A PO Boxes 25 The Esplanade           0.000000   
33                                    Studio District           0.000000   
34                The Annex, North Midtown, Yorkville           0.000000   
35                                        The Beaches           0.000000   
36                     The Beaches West, India Bazaar           0.000000   
37                       The Danforth West, Riverdale           0.000000   

    Airport  Airport Food Court  Airport Gate  Airport Lounge  \
0    0.0000              0.0000        0.0000          0.0000   
1    0.0000              0.0000        0.0000          0.0000   
2    0.0000              0.0000        0.0000          0.0000   
3    0.0000              0.0000        0.0000          0.0000   
4    0.0625              0.0625        0.0625          0.0625   
5    0.0000              0.0000        0.0000          0.0000   
6    0.0000              0.0000        0.0000          0.0000   
7    0.0000              0.0000        0.0000          0.0000   
8    0.0000              0.0000        0.0000          0.0000   
9    0.0000              0.0000        0.0000          0.0000   
10   0.0000              0.0000        0.0000          0.0000   
11   0.0000              0.0000        0.0000          0.0000   
12   0.0000              0.0000        0.0000          0.0000   
13   0.0000              0.0000        0.0000          0.0000   
14   0.0000              0.0000        0.0000          0.0000   
15   0.0000              0.0000    

In [76]:
len(allgrouped[allgrouped["Middle Eastern Restaurant"] > 0])


5

In [79]:
mediterranian_rests= allgrouped[["Neighborhoods","Middle Eastern Restaurant"]]
mediterranian_rests.head()

Neighborhoods  \
0                           Adelaide, King, Richmond   
1                                        Berczy Park   
2       Brockton, Exhibition Place, Parkdale Village   
3  Business Reply Mail Processing Centre 969 Eastern   
4  CN Tower, Bathurst Quay, Island airport, Harbo...   

   Middle Eastern Restaurant  
0                        0.0  
1                        0.0  
2                        0.0  
3                        0.0  
4                        0.0

#### Cluster Analysis
Run *k*-means to cluster the neighborhood into 5 clusters.

In [85]:
# set number of clusters
kclusters = 3

toronto_grouped_clustering = mediterranian_rests.drop('Neighborhoods', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 2, 0, 0, 0], dtype=int32)

In [86]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
new_one = mediterranian_rests.copy()

# add clustering labels
new_one["Cluster Labels"] = kmeans.labels_

In [87]:
new_one.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
new_one.head()

Neighborhood  \
0                           Adelaide, King, Richmond   
1                                        Berczy Park   
2       Brockton, Exhibition Place, Parkdale Village   
3  Business Reply Mail Processing Centre 969 Eastern   
4  CN Tower, Bathurst Quay, Island airport, Harbo...   

   Middle Eastern Restaurant  Cluster Labels  
0                        0.0               0  
1                        0.0               0  
2                        0.0               0  
3                        0.0               0  
4                        0.0               0

In [88]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
new_one = new_one.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(new_one.shape)
new_one.head()

(1686, 9)


Neighborhood  Middle Eastern Restaurant  Cluster Labels  \
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   
0  Adelaide, King, Richmond                        0.0               0   

   Neighborhood Latitude  Neighborhood Longitude  \
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   
0              43.650571              -79.384568   

                                         Venue  Venue Latitude  \
0  Four Seasons Centre for the Performing Arts       43.650592   
0                       Nathan Phillips Square       43.652270   
0                                    Rosalinda       43.650252   
0                     The Keg Steakhouse & Bar       43.649937   
0                           Shangri-La Toronto       43.649129   

   Venue Longitude                 Venue Category  
0       -79.385806                   Concert Hall  
0       -79.383516                          Plaza  
0       -79.385156  Vegetarian / Vegan Restaurant  
0       -79.384196                     Steakhouse  
0       -79.386557                          Hotel

In [89]:
# sort the results by Cluster Labels
new_one.sort_values(["Cluster Labels"], inplace=True)
new_one

Neighborhood  \
0                            Adelaide, King, Richmond   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfro

In [95]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(new_one['Neighborhood Latitude'], new_one['Neighborhood Longitude'], new_one['Neighborhood'], new_one['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [96]:
# save
map_clusters.save('map_clusters.html')

In [97]:
#First cluster
new_one.loc[new_one['Cluster Labels'] == 0]

Neighborhood  \
0                            Adelaide, King, Richmond   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
20  Harbourfront East, Toronto Islands, Union Station   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfront   
19                                       Harbourfro

In [98]:
#Second cluster
new_one.loc[new_one['Cluster Labels'] == 1]

Neighborhood  Middle Eastern Restaurant  Cluster Labels  \
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   
15  Dovercourt Village, Dufferin                   0.071429               1   

    Neighborhood Latitude  Neighborhood Longitude  \
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   
15              43.669005              -79.442259   

                              Venue  Venue Latitude  Venue Longitude  \
15  Planet Fitness Toronto Galleria       43.667588       -79.442574   
15           Blood Brothers Brewing       43.669944       -79.436533   
15                Rehearsal Factory       43.668877       -79.443603   
15          Happy Bakery & Pastries       43.667050       -79.441791   
15                         Parallel       43.669516       -79.438728   
15             The Greater Good Bar       43.669409       -79.439267   
15             Wallace Emerson Park       43.666933       -79.439449   
15               Shoppers Drug Mart       43.666745       -79.447446   
15                      Food Basics       43.666835       -79.446812   
15                           Rexall       43.667504       -79.442086   
15                  TD Canada Trust       43.667934       -79.441698   
15                    The Sovereign       43.673116       -79.440265   
15                          FreshCo       43.667918       -79.440754   
15                  Nova Era Bakery       43.669886       -79.437582   

               Venue Category  
15       Gym / Fitness Center  
15                    Brewery  
15                Music Venue  
15                     Bakery  
15  Middle Eastern Restaurant  
15                        Bar  
15                       Park  
15                   Pharmacy  
15                Supermarket  
15                   Pharmacy  
15                       Bank  
15                       Café  
15                Supermarket  
15                     Bakery

In [100]:
#Third cluster
new_one.loc[new_one['Cluster Labels'] == 2]

Neighborhood  Middle Eastern Restaurant  Cluster Labels  \
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
6         Central Bay Street                   0.023529               2   
30  Ryerson, Garden District                   0.030000               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District                   0.027027               2   
33           Studio District             